In [46]:
import pandas as pd

In [47]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [48]:
# importing

import sys
sys.path.append('../')
from breathworks.clustering.utils import get_data, go_to_data
from breathworks.clustering.bert import get_topics_prob
from breathworks.clustering.preprocessing import build_preprocessor
from breathworks.clustering.cleaning import clean_text, clean_data, clean_textual_columns, cleaning_advanced_column, cleaning_advanced_2
from breathworks.clustering.LDA import splitting_into_topics, lda_visual
from breathworks.clustering.clustering import plot_lda
from breathworks.clustering.config import drop_columns, textual_columns, categorical_columns, datetime_columns, column_pairs

In [49]:
# get the data

dataframe = get_data()
df_rem = go_to_data('remove2.csv')
df_combined = go_to_data('maybe_3_topic_label.csv')
row_labels_list = df_rem['Row Labels'].tolist()

/home/jonnyoh/.pyenv/versions/3.10.6/envs/lewagon/lib/python3.10/site-packages/pandas/core/frame.py:706: DeprecationWarning:

Passing a BlockManager to DataFrame is deprecated and will raise in a future version. Use public APIs instead.



In [50]:
# clean data

processed_data = clean_data(dataframe,drop_columns)
df_transformed = clean_textual_columns(processed_data, textual_columns)
df_transformed = cleaning_advanced_2(df_transformed, textual_columns, row_labels_list)

In [51]:
# clean data 2.0
advanced_cleaning_col= pd.Series(cleaning_advanced_column(df_combined['CustomerPurpose'], row_labels_list))
df_combined_final = advanced_cleaning_col.apply(clean_text)

In [52]:
# filter the df

in_person = ['IMfH', 'IMfS', 'I5DMfH']
online = ['OMfH', 'OMfS']
all_course_types = in_person + online
to_drop = ['Gender', 'CourseType', 'Ethnicity']
categorical_columns = [column for column in categorical_columns if column not in to_drop]
# df_filtered = df_transformed[(df_transformed['Gender'] == 'Male') &
#                                 (df_transformed['CourseType'].isin(all_course_types)) &
#                                 (df_transformed['Ethnicity'] == 'White')]

# df_filtered = df_filtered.drop(columns=to_drop)

# print(df_filtered.info())
# df_filtered.head(3)

In [53]:
# how many LDA topics per column

topics_per_column = {
    'PersonalHistory': 4,
    'Motivation': 4,
}

In [54]:
# Apply the transformations for LDA

df_transformed = df_transformed.drop(columns=to_drop, errors='ignore')

df_split, lda_details = splitting_into_topics(df_transformed,topics_per_column,textual_columns)
preprocessor = build_preprocessor(textual_columns, categorical_columns, datetime_columns)
df_LDA = preprocessor.fit_transform(df_split)

PersonalHistory
Topic 0:
[('anxiety', 99.38059361508033), ('depression', 63.74368948968855), ('suffer', 47.260564652863415), ('year', 47.209345438687414), ('time', 34.028302408253644), ('depression anxiety', 31.374845651803074), ('life', 30.760991201678973), ('mindfulness', 29.206074181019947), ('past', 28.68087599918067), ('help', 27.900001188330645)]
PersonalHistory
Topic 1:
[('acute', 58.047962401514546), ('mental', 54.92569666957557), ('mental health', 51.754716871825515), ('health', 49.45403041299762), ('condition', 48.52624995927403), ('debilitate', 48.20578632094311), ('health condition', 44.89680089788077), ('acute debilitate', 42.780615366013954), ('mental health condition', 42.60415673310811), ('experience', 41.87734193636879)]
PersonalHistory
Topic 2:
[('chronic', 22.377767102481826), ('mild', 21.65254094646327), ('anxiety', 19.543989072741606), ('pain', 16.784146516933873), ('syndrome', 16.661257236279095), ('depression', 14.899355646850136), ('migraine', 13.06937551009638)

In [55]:
# visualize the lda

lda_ph =lda_details['PersonalHistory']['lda']
x_ph = lda_details['PersonalHistory']['X']
vect_ph = lda_details['PersonalHistory']['vect']
lda_visual(lda_ph, x_ph, vect_ph)

In [56]:
# visualize the lda

lda_m =lda_details['Motivation']['lda']
x_m = lda_details['Motivation']['X']
vect_m = lda_details['Motivation']['vect']

lda_visual(lda_m, x_m, vect_m)

In [57]:
# getting final dataframe

transformed_columns = preprocessor.get_feature_names_out()
df_final = pd.DataFrame(df_LDA, columns=transformed_columns)
df_final = df_final.apply(pd.to_numeric)

In [58]:
# visualization

# df_3d = df_final[[col1a,col2a,col2b]]
# labelling_3d = fit_kmeans_and_label(df_3d,4)
# label_dataframe(df_3d, labelling_3d)
# print(df_3d.info())
# df_3d.head(3)

In [59]:
# plot_clusters_3d(df_3d,labelling_3d)

In [60]:
# plotting the clusters

plot_lda(df_final,column_pairs)

/home/jonnyoh/.pyenv/versions/3.10.6/envs/lewagon/lib/python3.10/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

/home/jonnyoh/.pyenv/versions/3.10.6/envs/lewagon/lib/python3.10/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



In [61]:
#init BERT

topics, probabilities, model = get_topics_prob(df_combined_final, 8)

2024-03-28 15:46:18,963 - BERTopic - Embedding - Transforming documents to embeddings.
2024-03-28 15:46:20,983 - BERTopic - Embedding - Completed ✓
2024-03-28 15:46:21,004 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-03-28 15:46:48,339 - BERTopic - Dimensionality - Completed ✓
2024-03-28 15:46:48,356 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-03-28 15:46:48,708 - BERTopic - Cluster - Completed ✓
2024-03-28 15:46:48,711 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-03-28 15:46:49,909 - BERTopic - Representation - Completed ✓
2024-03-28 15:46:49,912 - BERTopic - Topic reduction - Reducing number of topics
2024-03-28 15:46:50,425 - BERTopic - Topic reduction - Reduced number of topics from 71 to 8


In [62]:
# visualize BERT

model.visualize_topics()

/home/jonnyoh/.pyenv/versions/3.10.6/envs/lewagon/lib/python3.10/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

/home/jonnyoh/.pyenv/versions/3.10.6/envs/lewagon/lib/python3.10/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



In [63]:
# visualize BERT

model.visualize_barchart(top_n_topics=8)

/home/jonnyoh/.pyenv/versions/3.10.6/envs/lewagon/lib/python3.10/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

/home/jonnyoh/.pyenv/versions/3.10.6/envs/lewagon/lib/python3.10/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

